In [47]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

import json
import re
import ssl

import certifi
import networkx as nx

In [48]:
super_edges_temp = json.load(open("super_edges_temp.json","r", encoding="utf-8")) 
#słownik gdzie kluczami są super krawędzie a w liście krawędzie w środku tego połączenia

In [65]:
# super_edges_temp

In [51]:
#stworzyć słownik klucz -> mini krawędź, wartość -> super krawędź
# {'mini krwędź':'super krawędź'}

super_edge_list =list(super_edges_temp.items())

new_super_edges = {}
for e in range(len(super_edge_list)):
    one_edge = super_edge_list[e]
    big_edge = one_edge[0]
    small_edges = one_edge[-1]

    for i in range(len(small_edges)):
        new_super_edges[f'{small_edges[i]}'] = big_edge



In [ ]:
#zaczęłam ręcznie dodawać mini krawędzie z odpowiadającymi super krawędziami, ale to trochę nie ma sensu, takie rozwiązanie nie mając innego pomysłu xdd

new_super_edges['Kędzierzyn-Koźle_Zdzieszowice'] = 'Kędzierzyn-Koźle_Opole\xa0Główne'

new_super_edges['Ostrów\ax0Wielkopolski_Twardogóra'] = 'Ostrów\xa0Wielkopolski_Oleśnica\xa0Rataje'
new_super_edges['Twardogóra_Oleśnica\ax0Rataje'] = 'Ostrów\xa0Wielkopolski_Oleśnica\xa0Rataje'

new_super_edges['Oleśnica\ax0Rataje_Twardogóra'] = 'Oleśnica\xa0Rataje_Ostrów\xa0Wielkopolski'
new_super_edges['Twardogóra_Ostrów\ax0Wielkopolski'] = 'Oleśnica\xa0Rataje_Ostrów\xa0Wielkopolski'



In [66]:
len(new_super_edges) #chyba działa XDD
# ale nie jestem pewna, bo jest tylko 1044 elementów
# ale teoretycznie w tabeli mini krawedzie mogą się nam powtarzać, więc może być git
new_super_edges

{'Warszawa\xa0Wschodnia_Warszawa\xa0Centralna': 'Warszawa\xa0Wschodnia_Warszawa\xa0Zachodnia',
 'Warszawa\xa0Centralna_Warszawa\xa0Zachodnia': 'Warszawa\xa0Wschodnia_Warszawa\xa0Zachodnia',
 'Warszawa\xa0Zachodnia_Grodzisk\xa0Mazowiecki': 'Warszawa\xa0Zachodnia_Grodzisk\xa0Mazowiecki',
 'Grodzisk\xa0Mazowiecki_Opoczno\xa0Południe': 'Grodzisk\xa0Mazowiecki_Opoczno\xa0Południe',
 'Opoczno\xa0Południe_Włoszczowa\xa0Północ': 'Opoczno\xa0Południe_Włoszczowa\xa0Północ',
 'Włoszczowa\xa0Północ_Zawiercie': 'Włoszczowa\xa0Północ_Zawiercie',
 'Zawiercie_Dąbrowa\xa0Górnicza': 'Zawiercie_Dąbrowa\xa0Górnicza',
 'Dąbrowa\xa0Górnicza_Będzin\xa0Miasto': 'Dąbrowa\xa0Górnicza_Sosnowiec\xa0Główny',
 'Będzin\xa0Miasto_Sosnowiec\xa0Główny': 'Dąbrowa\xa0Górnicza_Sosnowiec\xa0Główny',
 'Sosnowiec\xa0Główny_Katowice': 'Sosnowiec\xa0Główny_Katowice',
 'Katowice_Tychy': 'Katowice_Tychy',
 'Tychy_Rybnik': 'Tychy_Rybnik',
 'Rybnik_Wodzisław\xa0Śląski': 'Rybnik_Chałupki',
 'Wodzisław\xa0Śląski_Chałupki': 'Rybnik_C

## próba dodania nowej kolumny z super krawędziami

In [53]:
df = pd.read_csv("data/connections_test2.csv",encoding="utf-8-sig")

In [54]:
df_uniq = df.drop_duplicates(
  subset = ['stacja_wyjazdu','stacja_przyjazdu'],
  keep = 'last').reset_index(drop = True)

In [57]:
len(df_uniq)
df_uniq.head(5)

Unnamed: 0        nazwa_pociagu       stacja_wyjazdu     stacja_przyjazdu  \
0        5024  ECE 14000/1 SILESIA  Grodzisk Mazowiecki     Opoczno Południe   
1       36335  ECE 14002/3 POLONIA             Pszczyna         Zebrzydowice   
2       36336  ECE 14002/3 POLONIA         Zebrzydowice  Petrovice u Karvine   
3       36796   ECE 14004/5 BATORY             Terespol       Biała Podlaska   
4       36801   ECE 14004/5 BATORY     Mińsk Mazowiecki     Warszawa Gdańska   

    data czas_rozkladowy  opoznienie  opoznienie_netto  
0  24.03           06:20         0.0               3.0  
1  24.03           10:08         4.0               4.0  
2  24.03           10:18         1.0              -3.0  
3  24.03           06:27         0.0               0.0  
4  24.03           08:12         7.0               4.0

In [ ]:
# new_super_edges

In [ ]:
# # działa
# def add_super_edge(df,new_super_edges):
    
#     old_edges = df['stacja_wyjazdu'] + '_'+ df['stacja_przyjazdu']
#     for row in range(len(old_edges)):
#         for edge in list(new_super_edges.keys()):
#             # print(edge)
#             if edge == old_edges[row]:
#                 df.at[row,'super_krawedz'] = new_super_edges[edge]
#                 # print(old_edges[row],'--->',new_super_edges[edge])
#             else:
#                 pass
#     return df

  
# #4m53.6s - dla wszystkich danych

In [58]:
def add_super_edge(df,new_super_edges,super_edges_temp):
    super_edges_list = list(super_edges_temp.keys()) # super krawędzie lista

    old_edges = df['stacja_wyjazdu'] + '_'+ df['stacja_przyjazdu']
    for row in range(len(old_edges)):
        for edge in list(new_super_edges.keys()):
            # print(edge)
            if edge == old_edges[row]:
                df.at[row,'super_krawedz'] = new_super_edges[edge]
                print(old_edges[row],'--->',new_super_edges[edge])
            elif old_edges[row] in super_edges_list: #sprawdzam, czy połączenie jest może jednak super krawędzią, której nie ma w mini krawędziach
                df.at[row,'super_krawedz'] =  old_edges[row]
                print('Should work')

            else:
                # print("nic")
                #trzeba zrobić coś w zamian, jak nie będzie takiej mini krawędzi w naszym słowniku
                #choć tak nie powinno się zdarzyć
                # df['super_krawedz'] = NUL
                pass
    return df

  
#4m53.6s - dla wszystkich danych

In [ ]:
# df_uniq

In [59]:
df_uniq_super = add_super_edge(df_uniq, new_super_edges,super_edges_temp)

Should work
Should work
Should work
Grodzisk Mazowiecki_Opoczno Południe ---> Grodzisk Mazowiecki_Opoczno Południe
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should work
Should wo

In [63]:
# df_uniq_super
df_uniq_super[df_uniq_super['super_krawedz'].isna()]  #96 wieszy nie ma przypisanej super krawedzi
# 42 wiesze NaN
# w drugim słowniku nie ma niektórych mini krawędzi w drugą stronę
# np Zdzieszowice_Kędzierzyn-Koźle	jest, ale Kędzierzyn-Koźle_Zdzieszowice nie ma



Unnamed: 0             nazwa_pociagu       stacja_wyjazdu  \
140       52025       EIJ 5620/1 SŁOWACKI  Ostrów Wielkopolski   
141       52026       EIJ 5620/1 SŁOWACKI           Twardogóra   
160       60872       EIJ 6521/0 SŁOWACKI      Oleśnica Rataje   
161       60873       EIJ 6521/0 SŁOWACKI           Twardogóra   
219        7628    MPE 12100/1 CHEŁMIANIN   Warszawa Wschodnia   
220        7629    MPE 12100/1 CHEŁMIANIN               Otwock   
274         469     MPE 18108/9 WŁÓKNIARZ          Łódź Chojny   
275         470     MPE 18108/9 WŁÓKNIARZ        Łódź Retkinia   
286       61862      MPE 25100/1 KUJAWIAK               Pilawa   
287       61863      MPE 25100/1 KUJAWIAK               Otwock   
335       30853      MPE 37104/5 MEHOFFER     Przemyśl Zasanie   
336       30854      MPE 37104/5 MEHOFFER              Radymno   
424       41761  MPE 48102/3 SZYNDZIELNIA     Kędzierzyn-Koźle   
425       41762  MPE 48102/3 SZYNDZIELNIA         Zdzieszowice   
426       41763  MPE 48102/3 SZYNDZIELNIA              Gogolin   
504       11024     MPE 61103/2 DĄBROWSKA           Szepietowo   
505       11025     MPE 61103/2 DĄBROWSKA             Szymbory   
506       11027     MPE 61103/2 DĄBROWSKA             Racibory   
507       11028     MPE 61103/2 DĄBROWSKA          Zdrody Nowe   
508       11029     MPE 61103/2 DĄBROWSKA            Łapy Osse   
536       36201       MPE 68103/2 SZKUNER               Leszno   
537       36202       MPE 68103/2 SZKUNER              Kościan   
542       36207       MPE 68103/2 SZKUNER          Piła Główna   
543       36208       MPE 68103/2 SZKUNER            Jastrowie   
554       48303      MPE 68105/4 SWAROŻYC             Kostrzyn   
555       48304      MPE 68105/4 SWAROŻYC          Mieszkowice   
575        7463      MPE 73104/5 MEHOFFER             Jarosław   
576        7464      MPE 73104/5 MEHOFFER              Radymno   
644       68083        MPE 83100/1 GÓRSKI        Poznań Główny   
645       68084        MPE 83100/1 GÓRSKI             Swarzędz   
740        3265       MPE 86103/2 SZKUNER           Szczecinek   
741        3266       MPE 86103/2 SZKUNER            Jastrowie   
746        3271       MPE 86103/2 SZKUNER        Poznań Główny   
747        3272       MPE 86103/2 SZKUNER              Kościan   
756       18045      MPE 86104/5 SWAROŻYC               Chojna   
757       18046      MPE 86104/5 SWAROŻYC          Mieszkowice   
830       44396      MPJ 26102/3 MORCINEK                Brzeg   
831       44397      MPJ 26102/3 MORCINEK                Oława   
855       53720      MPJ 62102/3 MORCINEK       Wrocław Główny   
856       53721      MPJ 62102/3 MORCINEK                Oława   
879       70089     MPJ 81108/9 WŁÓKNIARZ            Pabianice   
880       70090     MPJ 81108/9 WŁÓKNIARZ        Łódź Retkinia   

        stacja_przyjazdu   data czas_rozkladowy  opoznienie  opoznienie_netto  \
140           Twardogóra  24.03           13:58        16.0               2.0   
141      Oleśnica Rataje  24.03           14:13        16.0               0.0   
160           Twardogóra  24.03           14:19        10.0              10.0   
161  Ostrów Wielkopolski  24.03           14:51        13.0               3.0   
219               Otwock  24.03           07:14         0.0               0.0   
220               Pilawa  24.03           07:28         0.0               0.0   
274        Łódź Retkinia  24.03           06:08         0.0              -1.0   
275            Pabianice  24.03           06:18         0.0               0.0   
286               Otwock  24.03           15:43         0.0               0.0   
287   Warszawa Wschodnia  24.03           16:06         0.0               0.0   
335              Radymno  24.03           12:20         0.0               0.0   
336             Jarosław  24.03           12:30         2.0               2.0   
424         Zdzieszowice  24.03           10:21        -4.0              -9.0   
425              Gogolin  24.03 

In [ ]:
# len(df_head) #71228 wśród wszystkich danych - tyle pustych krawędzi

In [ ]:
# df_uniq_super[df_uniq_super['stacja_wyjazdu']== 'Tczew'] 

In [ ]:
# list(super_edges_temp.keys())

In [ ]:
#jeszcze raz przypisanie, tylko teraz do wierszy gdzie są NaN wartości
#i będę szukać po kluczach, tylko że tego pierwszego słownika
# i przypisywać klucze (bo w pierwszym słowniku to klucze są super krawędziami)

#zostawie na później może


# NIE DZIAŁA
# super_edges = list(super_edges_temp.keys())

# def add_missing_super(df,list_super_edges):
#     """
#     @df: data.frame z kolumną 'stacja_przyjazdu', gdzie znajdują się brakujące super_krawędzie
#     """
#     df_nan = df[df['super_krawedz'].isna()] 

#     old_edges = df['stacja_wyjazdu'] + '_'+ df['stacja_przyjazdu']
#     for row in range(len(old_edges)):
#         for edge in list(new_super_edges.keys()):
#             # print(edge)
#             if edge == old_edges[row]:
#                 df.at[row,'super_krawedz'] = new_super_edges[edge]
#                 print(old_edges[row],'--->',new_super_edges[edge])
#             else:
#                 pass